In [1]:
"""
Author(s): Steven van den Broek, Yuqin Cui
Created: 2019-05-05
Edited: 2019-05-05
"""

In [58]:
import numpy as np
import pandas as pd
import panel as pn
import param
import hvplot.pandas
from colorcet import palette

In [40]:
fname = 'GephiMatrix_author_similarity.csv'
f = open(fname, 'r')

# Get author names
line1 = f.readline()
names = line1[1:].split(';');

seen = {}
dupes = []

for index, name in enumerate(names):
    if name not in seen:
        seen[name] = 1
    else:
        if seen[name] == 1:
            dupes.append((index, name))
        seen[name] += 1

# add 1, 2 etc after the name
for pair in dupes:
    index = pair[0]
    name = pair[1]
    for i in range(seen[name]):
        names[index] = name + str((i+1))
        #print(names[index])

# Read csv
df = pd.read_csv(f, names=names, sep=';')

# Fix it
df = df.reset_index(level=1)
names.append("delete")
names = [name.replace('_', ' ') for name in names]
df.columns = names
del df["delete"]
df.set_index([df.columns], inplace=True)

# Get names again for later use
names = df.columns.tolist()

# Get 150*150 sub matrix since otherwise the plot is very slow..
df = df.head(150)[names[0:150]]
names = df.columns.tolist()
df.head()

Jim Thomas  Eleftherios Koutsofios  Lawrence A. Rowe  \
Jim Thomas                1.000000                0.097384          0.125630   
Eleftherios Koutsofios    0.097384                1.000000          0.223607   
Lawrence A. Rowe          0.125630                0.223607          1.000000   
Jonathan I. Helfman       0.109691                0.144620          0.242536   
Mary Brewster             0.275405                0.281718          0.094491   

                        Jonathan I. Helfman  Mary Brewster  Min Chen  \
Jim Thomas                         0.109691       0.275405  0.195006   
Eleftherios Koutsofios             0.144620       0.281718  0.235008   
Lawrence A. Rowe                   0.242536       0.094491  0.181902   
Jonathan I. Helfman                1.000000       0.229175  0.294118   
Mary Brewster                      0.229175       1.000000  0.297927   

                        Christopher G. Healey  Mac Holden   M. Gray  \
Jim Thomas                           0.196239    0.317986  0.407599   
Eleftherios Koutsofios               0.383180    0.365148  0.132508   
Lawrence A. Rowe                     0.123579    0.255155  0.027778   
Jonathan I. Helfman                  0.173840    0.049507  0.053897   
Mary Brewster                        0.336302    0.115728  0.356966   

                        Jason Stewart  ...  Daniel Keim  Kenneth Utting  \
Jim Thomas                        0.0  ...     0.098332        0.311889   
Eleftherios Koutsofios            0.0  ...     0.115145        0.172133   
Lawrence A. Rowe                  0.0  ...     0.080920        0.072169   
Jonathan I. Helfman               0.0  ...     0.064230        0.525105   
Mary Brewster                     0.0  ...     0.175167        0.245495   

                        Ted Selker  Gabor T. Herman  Laxmi Parida  \
Jim Thomas                0.179382         0.235521      0.185396   
Eleftherios Koutsofios    0.201843         0.426963      0.172848   
Lawrence A. Rowe          0.246183         0.292925      0.052705   
Jonathan I. Helfman       0.417957         0.284179      0.076696   
Mary Brewster             0.255883         0.319844      0.099602   

                        Jeannine Pinto  Jonathan Furner  Clayton Lewis  \
Jim Thomas                    0.134840         0.147984       0.279826   
Eleftherios Koutsofios        0.000000         0.400819       0.434813   
Lawrence A. Rowe              0.000000         0.128037       0.220971   
Jonathan I. Helfman           0.000000         0.341589       0.064312   
Mary Brewster                 0.253546         0.338754       0.150334   

                        Francis P. Boscoe  Ian M. Soboroff  
Jim Thomas                       0.262875         0.058026  
Eleftherios Koutsofios           0.225279         0.258199  
Lawrence A. Rowe                 0.087186         0.072169  
Jonathan I. Helfman              0.225554         0.350070  
Mary Brewster                    0.483312         0.163663  

[5 rows x 150 columns]

In [41]:
solid = df.reset_index()
liquid = solid.melt(id_vars='index', value_vars=list(df.columns[1:]), value_name="Similarity", var_name="name2")
liquid.columns = ['name1', 'name2', 'similarity']
liquid.head()

name1                   name2  similarity
0              Jim Thomas  Eleftherios Koutsofios    0.097384
1  Eleftherios Koutsofios  Eleftherios Koutsofios    1.000000
2        Lawrence A. Rowe  Eleftherios Koutsofios    0.223607
3     Jonathan I. Helfman  Eleftherios Koutsofios    0.144620
4           Mary Brewster  Eleftherios Koutsofios    0.281718

In [42]:
liquid.hvplot.heatmap('name1', 'name2', 'similarity',
                      height=500, width=600, flip_yaxis=True, xaxis=None, yaxis=None)

:HeatMap   [name1,name2]   (similarity)

In [43]:
#convert similarity into unsimilarity (1.0 - similarity)
for name in names:
    df[name] = 1 - df[name]
df.head()

Jim Thomas  Eleftherios Koutsofios  Lawrence A. Rowe  \
Jim Thomas                0.000000                0.902616          0.874370   
Eleftherios Koutsofios    0.902616                0.000000          0.776393   
Lawrence A. Rowe          0.874370                0.776393          0.000000   
Jonathan I. Helfman       0.890309                0.855380          0.757464   
Mary Brewster             0.724595                0.718282          0.905509   

                        Jonathan I. Helfman  Mary Brewster  Min Chen  \
Jim Thomas                         0.890309       0.724595  0.804994   
Eleftherios Koutsofios             0.855380       0.718282  0.764992   
Lawrence A. Rowe                   0.757464       0.905509  0.818098   
Jonathan I. Helfman                0.000000       0.770825  0.705882   
Mary Brewster                      0.770825       0.000000  0.702073   

                        Christopher G. Healey  Mac Holden   M. Gray  \
Jim Thomas                           0.803761    0.682014  0.592401   
Eleftherios Koutsofios               0.616820    0.634852  0.867492   
Lawrence A. Rowe                     0.876421    0.744845  0.972222   
Jonathan I. Helfman                  0.826160    0.950493  0.946103   
Mary Brewster                        0.663698    0.884272  0.643034   

                        Jason Stewart  ...  Daniel Keim  Kenneth Utting  \
Jim Thomas                        1.0  ...     0.901668        0.688111   
Eleftherios Koutsofios            1.0  ...     0.884855        0.827867   
Lawrence A. Rowe                  1.0  ...     0.919080        0.927831   
Jonathan I. Helfman               1.0  ...     0.935770        0.474895   
Mary Brewster                     1.0  ...     0.824833        0.754505   

                        Ted Selker  Gabor T. Herman  Laxmi Parida  \
Jim Thomas                0.820618         0.764479      0.814604   
Eleftherios Koutsofios    0.798157         0.573037      0.827152   
Lawrence A. Rowe          0.753817         0.707075      0.947295   
Jonathan I. Helfman       0.582043         0.715821      0.923304   
Mary Brewster             0.744117         0.680156      0.900398   

                        Jeannine Pinto  Jonathan Furner  Clayton Lewis  \
Jim Thomas                    0.865160         0.852016       0.720174   
Eleftherios Koutsofios        1.000000         0.599181       0.565187   
Lawrence A. Rowe              1.000000         0.871963       0.779029   
Jonathan I. Helfman           1.000000         0.658411       0.935688   
Mary Brewster                 0.746454         0.661246       0.849666   

                        Francis P. Boscoe  Ian M. Soboroff  
Jim Thomas                       0.737125         0.941974  
Eleftherios Koutsofios           0.774721         0.741801  
Lawrence A. Rowe                 0.912814         0.927831  
Jonathan I. Helfman              0.774446         0.649930  
Mary Brewster                    0.516688         0.836337  

[5 rows x 150 columns]

In [44]:
#This is just the method online: https://gmarti.gitlab.io/ml/2017/09/07/how-to-sort-distance-matrix.html
#We have to clean data and modified the method

import numpy as np
from scipy.spatial.distance import pdist, squareform
from sklearn import datasets
from fastcluster import linkage
dist_mat = squareform(pdist(df))

In [45]:
def seriation(Z,N,cur_index):
    '''
        input:
            - Z is a hierarchical tree (dendrogram)
            - N is the number of points given to the clustering process
            - cur_index is the position in the tree for the recursive traversal
        output:
            - order implied by the hierarchical tree Z
            
        seriation computes the order implied by a hierarchical tree (dendrogram)
    '''
    if cur_index < N:
        return [cur_index]
    else:
        left = int(Z[cur_index-N,0])
        right = int(Z[cur_index-N,1])
        return (seriation(Z,N,left) + seriation(Z,N,right))
    
def compute_serial_matrix(dist_mat,method="ward"):
    '''
        input:
            - dist_mat is a distance matrix
            - method = ["ward","single","average","complete"]
        output:
            - seriated_dist is the input dist_mat,
              but with re-ordered rows and columns
              according to the seriation, i.e. the
              order implied by the hierarchical tree
            - res_order is the order implied by
              the hierarhical tree
            - res_linkage is the hierarhical tree (dendrogram)
        
        compute_serial_matrix transforms a distance matrix into 
        a sorted distance matrix according to the order implied 
        by the hierarchical tree (dendrogram)
    '''
    N = len(dist_mat)
    flat_dist_mat = squareform(dist_mat)
    res_linkage = linkage(flat_dist_mat, method=method,preserve_input=True)
    res_order = seriation(res_linkage, N, N + N-2)
    seriated_dist = np.zeros((N,N))
    a,b = np.triu_indices(N,k=1)
    seriated_dist[a,b] = dist_mat[ [res_order[i] for i in a], [res_order[j] for j in b]]
    seriated_dist[b,a] = seriated_dist[a,b]
    
    return seriated_dist, res_order, res_linkage

In [52]:
ordered_dist_mat = {}
ordered_dist_mat['ward'], res_order, res_linkage = compute_serial_matrix(dist_mat,"ward")
ordered_dist_mat['single'], res_order, res_linkage = compute_serial_matrix(dist_mat,"single")
ordered_dist_mat['average'], res_order, res_linkage = compute_serial_matrix(dist_mat,"average")
ordered_dist_mat['complete'], res_order, res_linkage = compute_serial_matrix(dist_mat,"complete")

solid = pd.DataFrame(ordered_dist_mat['ward'])
solid.index = names
solid.columns = names
solid

Jim Thomas  Eleftherios Koutsofios  Lawrence A. Rowe  \
Jim Thomas                0.000000                1.243522          1.555156   
Eleftherios Koutsofios    1.243522                0.000000          2.040694   
Lawrence A. Rowe          1.555156                2.040694          0.000000   
Jonathan I. Helfman       1.295865                2.037526          1.766817   
Mary Brewster             1.851939                2.061392          2.327296   
Min Chen                  2.124743                2.378482          2.129100   
Christopher G. Healey     2.512458                2.826163          2.773459   
Mac Holden                2.218384                2.551903          2.395397   
M. Gray                   1.926663                1.998967          2.584579   
Jason Stewart             2.371333                2.665069          2.276586   
Volker Vogelmann          2.346198                2.579029          1.978910   
Benjamin B. Bederson      2.305101                2.464014          1.955728   
Maureen Tingley           2.142774                2.221540          2.284105   
C. K. Yung                2.445833                2.814531          2.351779   
S. Joy Mountford          2.404061                2.657933          2.307729   
L. D. Bergman             2.025384                2.568621          2.460164   
Rich Gossweiler           2.340714                2.827066          2.393815   
M. Maruyama               2.737312                3.310212          2.951083   
David P. Helmbold         2.505790                2.949127          2.573941   
C. Dunmire                2.536710                3.049037          2.826904   
C. C. Gomberg             2.192180                2.508337          2.275206   
Allison Woodruff          2.312065                2.848617          2.449289   
Karlis Kaugars            2.606907                3.048649          2.456332   
Jeffrey Brainerd          2.738641                3.231485          2.720507   
Claudia Schmid            2.449691                2.909156          2.630666   
Ken Perrine               2.524277                3.116019          2.659432   
Ishantha Lokuge           2.577896                3.099182          2.463289   
M. Weiser                 2.453904                2.914000          2.532017   
Kevin Teixeira            2.445895                2.841442          2.816989   
FranÃ§ois Robillard       2.026549                2.480208          2.153509   
...                            ...                     ...               ...   
Dave Wroblewski           2.332576                2.523341          2.121498   
R. Mitchell               2.318187                2.522982          2.141655   
Ken-ichi Okada            2.359964                2.666215          2.258482   
Bruce Hendrickson         2.280865                2.670437          2.564178   
Mike Craven               2.413345                2.826996          2.427998   
Randall B. Smith          2.359841                2.761295          2.443295   
Aristides Gionis          2.380224                2.609265          2.461671   
Blaine A. Price           2.438840                2.717019          2.374207   
Yoram Moses               2.258738                2.366335          2.107638   
David Ungar               2.447790                2.657634          2.016197   
Andrew W. Appel           2.141371                2.454722          1.979280   
Henry Lieberman           2.190857                2.243543          2.432959   
Kenneth P. Birman         2.180852                2.461588          2.384087   
Marc Levoy                2.605242                2.678585          2.564570   
Dan Gusfield              2.676522                2.667129          2.566782   
Gareth Smith              2.546729                2.759158          2.089262   
R. Kevin McCabe           2.919305                2.892662          2.483978   
Masahiro Takatsuka        2.201681                2.567130          2.107676   
Brad A. Myers           

In [65]:
pn.extension()

class Matrix_dropdown(param.Parameterized):
    reordering = param.ObjectSelector(default="ward",objects=["ward","single","average","complete"])
    
    def view(self):
        solid = pd.DataFrame(ordered_dist_mat[self.reordering])
        solid.index = names
        solid.columns = names
        solid.reset_index(inplace=True)
        liquid = solid.melt(id_vars='index', value_vars=list(df.columns[1:]), var_name="name2")
        liquid.columns = ['name1', 'name2', 'distance']
        return liquid.hvplot.heatmap('name1', 'name2', 'distance',
                      height=500, width=600, flip_yaxis=True, xaxis=None, yaxis=None, cmap=palette['kbc'])

matrix = Matrix_dropdown(name='Adjacency Matrix')
from bokeh.embed import components
pn.Column(matrix.param, matrix.view)

Column
    [0] Column(name='Param16705', width=300)
        [0] StaticText(value='<b>Adjacency Matrix</b>')
        [1] Select(name='Reordering', options=OrderedDict([('ward', ...]), value='ward')
    [1] ParamMethod(method)